In [1]:
import gensim
import json
import re
from nltk.tokenize import word_tokenize
from pymorphy2 import MorphAnalyzer
# import pyLDAvis.gensim 
morph = MorphAnalyzer()

In [2]:
def remove_tags(text):
    return re.sub(r'<[^>]+>', '', text)

def clean(words):
    clean = [morph.parse(word)[0].normal_form for word in words if len(set(word)) > 1]
    return clean

## Данные

Возьмем 4 тыс статьи с Хабра. Это мало для хорошей тематической модели, но иначе у нас просто ничего не обучится за семинар.

In [3]:
texts = open('habr_texts.txt').read().splitlines()

В текстах есть тэги. Потрем их. Ещё токенизируем самым простым способом и нормализуем Pymorphy.

In [4]:
texts = [clean(word_tokenize(text.lower())) for text in texts]

In [15]:
# для нграммов
# ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4)
# p = gensim.models.phrases.Phraser(ph)

### Тематическое моделирование в gensim

Для моделей нужно сделать словарь.

In [5]:
dictinary = gensim.corpora.Dictionary(texts)

In [6]:
dictinary.filter_extremes(no_above=0.3, no_below=10)
dictinary.compactify()

In [7]:
print(dictinary)

Dictionary(16147 unique tokens: ['позиция', 'below', 'масштабироваться', 'заседание', 'односторонний']...)


Преобразуем наши тексты в мешки слов. 

In [9]:
corpus = [dictinary.doc2bow(text) for text in texts]
# если текстов много, то тут может быть генератор

In [11]:
lda = gensim.models.LdaMulticore(corpus, 30, id2word=dictinary, passes=1) # если поддерживается многопоточность
# lsi = gensim.models.LdaModel(200, id2word=dictinary, passes=5)

Посмотрим на топики.

In [13]:
lda.print_topics()

[(18,
  '0.014*"gt" + 0.013*"lt" + 0.003*"return" + 0.003*"файл" + 0.002*"игра" + 0.002*"if" + 0.002*"база" + 0.002*"выбрать" + 0.002*"сервис" + 0.002*"метод"'),
 (0,
  '0.005*"lt" + 0.004*"gt" + 0.004*"устройство" + 0.003*"файл" + 0.002*"ошибка" + 0.002*"amp" + 0.002*"игра" + 0.002*"the" + 0.002*"значение" + 0.002*"for"'),
 (14,
  '0.011*"gt" + 0.008*"lt" + 0.003*"if" + 0.003*"public" + 0.003*"сервер" + 0.003*"int" + 0.003*"метод" + 0.003*"сеть" + 0.002*"программа" + 0.002*"return"'),
 (24,
  '0.008*"gt" + 0.006*"lt" + 0.002*"сервер" + 0.002*"сеть" + 0.002*"if" + 0.002*"язык" + 0.002*"клиент" + 0.002*"модель" + 0.002*"файл" + 0.002*"устройство"'),
 (16,
  '0.011*"gt" + 0.008*"lt" + 0.003*"сеть" + 0.003*"сайт" + 0.003*"устройство" + 0.003*"точка" + 0.003*"игра" + 0.002*"сервер" + 0.002*"технология" + 0.002*"файл"'),
 (23,
  '0.011*"gt" + 0.006*"lt" + 0.003*"файл" + 0.002*"устройство" + 0.002*"if" + 0.002*"значение" + 0.002*"метод" + 0.002*"сеть" + 0.002*"return" + 0.002*"продукт"'),
 (

Ещё есть штука для визуализации.

In [14]:
pyLDAvis.enable_notebook()

NameError: name 'pyLDAvis' is not defined

In [25]:
pyLDAvis.gensim.prepare(lda, corpus, dictinary)

PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
39     5.207283        1       1 -0.104942 -0.034940
66     4.615097        1       2 -0.132241 -0.011633
32     4.169844        1       3 -0.122827  0.025487
76     3.926425        1       4 -0.153326  0.027399
9      3.161294        1       5  0.148581 -0.026019
69     3.107751        1       6 -0.087693 -0.020076
42     3.053883        1       7 -0.131450  0.108497
17     3.036601        1       8 -0.106548 -0.015699
11     2.875589        1       9  0.211465  0.034850
21     2.833369        1      10 -0.168317 -0.106137
99     2.347564        1      11 -0.050404 -0.042571
95     2.167069        1      12  0.250924 -0.068734
24     2.085184        1      13  0.050898  0.169442
55     1.910081        1      14  0.013885 -0.137580
82     1.831595        1      15 -0.013532  0.104547
33     1.731326        1      16  0.265381  0.013160
2      1.673731        1      17  0.031570 -0.027448
12     1.558380        1      18 -0.056228 -0.007012
44     1.546106        1      19 -0.111054  0.035288
72     1.377197        1      20 -0.087347 -0.053829
53     1.364835        1      21 -0.038686 -0.031293
7      1.361281        1      22  0.216468 -0.164497
45     1.338955        1      23 -0.129026 -0.017576
80     1.336562        1      24 -0.030752  0.072616
1      1.278423        1      25  0.219613  0.107940
13     1.248719        1      26 -0.095678 -0.077858
83     1.244555        1      27 -0.121666 -0.162371
23     1.220472        1      28  0.148626 -0.043880
5      1.148246        1      29  0.074308  0.090692
58     1.031209        1      30  0.043162 -0.068166
...         ...      ...     ...       ...       ...
77     0.306102        1      71 -0.065431  0.042181
79     0.304008        1      72 -0.030596  0.039909
34     0.297796        1      73 -0.016032 -0.089186
65     0.294032        1      74 -0.017852 -0.045839
26     0.287487        1      75  0.133430 -0.054679
73     0.280661        1      76 -0.018535  0.005688
25     0.278877        1      77 -0.043292  0.000024
63     0.269739        1      78  0.042492  0.000783
41     0.263313        1      79 -0.109963  0.023253
68     0.256060        1      80 -0.046270 -0.100824
87     0.252922        1      81 -0.065677 -0.099800
19     0.252630        1      82  0.112867  0.042308
18     0.229104        1      83  0.077160 -0.000801
93     0.225715        1      84 -0.021871 -0.054356
71     0.225424        1      85  0.002733 -0.010247
86     0.225374        1      86  0.026604 -0.005454
43     0.224352        1      87  0.097630  0.015679
91     0.211842        1      88 -0.055621  0.024366
96     0.211689        1      89 -0.087494  0.016726
51     0.198935        1      90 -0.050849 -0.018857
0      0.185554        1      91 -0.023484  0.012822
3      0.181172        1      92 -0.065739  0.008608
46     0.173898        1      93  0.131793 -0.017906
90     0.159366        1      94 -0.086584 -0.034519
35     0.153680        1      95 -0.040757 -0.003912
22     0.143383        1      96 -0.019634  0.076609
84     0.142823        1      97 -0.008315 -0.031326
89     0.125005        1      98 -0.034021  0.008001
49     0.114128        1      99 -0.017692 -0.002315
92     0.100717        1     100 -0.058452 -0.022046

[100 rows x 5 columns], topic_info=       Category          Freq           Term         Total  loglift  logprob
term                                                                        
13968   Default  13470.000000             gt  13470.000000  30.0000  30.0000
11355   Default   5563.000000          gt_lt   5563.000000  29.0000  29.0000
10126   Default   5348.000000           игра   5348.000000  28.0000  28.0000
7905    Default   6634.000000             lt   6634.000000  27.0000  27.0000
10865   Default   5339.000000           файл   5339.000000  26.0000  26.0000
8377    Default   4862.000000     устройство   4862.000

Можно посмотреть метрики.

In [16]:
lda.log_perplexity(corpus[:100], total_docs=100)

-25.231083844142873

In [17]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [19]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=10, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [20]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [21]:
coherence_model_lda.get_coherence()

0.4194483241023404

### Разложение матриц в sklearn

In [22]:
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import pandas as pd

Sklearn принимает на вход строки, поэтому склеим наши списки.

In [23]:
stexts = [' '.join(text) for text in texts]

Сделаем матрицу слова-документы с помощью TfidfVectorizer

In [26]:
vectorizer = TfidfVectorizer(max_features=25000, min_df=5, max_df=0.3, lowercase=False)
X = vectorizer.fit_transform(stexts)

Разложим её.

In [27]:
model = NMF(n_components=30)

In [28]:
model.fit(X)

NMF(alpha=0.0, beta_loss='frobenius', init=None, l1_ratio=0.0, max_iter=200,
  n_components=30, random_state=None, shuffle=False, solver='cd',
  tol=0.0001, verbose=0)

In [35]:
def get_nmf_topics(model, n_top_words):
    
    #id слов.
    feat_names = vectorizer.get_feature_names()
    
    word_dict = {};
    for i in range(30):
        
        #топ n слов для темы.
        words_ids = model.components_[i].argsort()[:-n_top_words - 1:-1]
        words = [feat_names[key] for key in words_ids]
        word_dict['Topic # ' + '{:02d}'.format(i+1)] = words;
    
    return pd.DataFrame(word_dict);

In [36]:
get_nmf_topics(model, 10)

Topic # 01 Topic # 02 Topic # 03   Topic # 04 Topic # 05  Topic # 06  \
0           ты         gt       игра  космический     объект       товар   
1      продукт         lt      игрок      спутник   значение      скидка   
2    сотрудник        div    игровой       орбита    элемент     магазин   
3       бизнес      class     играть       ракета     строка        цена   
4  программист       name   персонаж         марс      метод       рубль   
5       клиент       this      steam      аппарат       блок       рынок   
6       деньга      props   геймплей        земля       файл      россия   
7         опыт     return      unity         луна      класс  российский   
8     менеджер       html       жанр         наса       язык     покупка   
9           да      value       инди        полёт   алгоритм       налог   

    Topic # 07  Topic # 08  Topic # 09        Topic # 10     ...       \
0       камера          js     android               php     ...        
1   устройство       react      google              язык     ...        
2     смартфон         css         ios           symfony     ...        
3      телефон  javascript   мобильный               yii     ...        
4  аккумулятор     angular         app           laravel     ...        
5       датчик         веб  устройство                go     ...        
6        видео         vue       swift               api     ...        
7        экран     браузер        play  программирование     ...        
8       корпус   компонент        view              java     ...        
9        карта        html      gradle                gt     ...        

      Topic # 21        Topic # 22 Topic # 23      Topic # 24  Topic # 25  \
0       обучение             книга       файл           центр         бот   
1          робот              часы     docker            дата    telegram   
2      нейросеть          каковать       sudo          услуга   сообщение   
3           сеть   порекомендовать       http  инфраструктура    телеграм   
4      интеллект  профессиональный        etc        облачный         чат   
5      нейронный             каким      nginx    оборудование         bot   
6       машинный      предпочитать     скрипт          клиент         api   
7       алгоритм           слушать        usr          сервис  мессенджер   
8  искусственный          бумажный        amp          облако       канал   
9           язык              путь        bin             цод     message   

     Topic # 26          Topic # 27 Topic # 28 Topic # 29   Topic # 30  
0          звук           процессор       сайт         if           vr  
1        сигнал               intel   страница        int  виртуальный  
2       наушник              память    реклама        amp   реальность  
3     усилитель                диск     клиент         lt       oculus  
4       частота                ядро    контент     return         шлем  
5     искажение                  гб    браузер       null         vive  
6      звуковой  производительность     google       else          htc  
7        музыка             ноутбук     письмо       char       unreal  
8  акустический                 ssd  рекламный       void    дополнить  
9      диапазон          видеокарта      домен        std       дизайн  

[10 rows x 30 columns]